# Box Rectification & Augmentation *(debug v2)*

Extra diagnostics to explain **where cropping goes wrong** and to display key COCO fields for every patch:
* verbose per‑annotation banner with image/annotation IDs & bbox details
* lost‑pixels report when a crop gets clipped by image borders
* `inspect()` prints the category, bbox, rotation and lost‑pixel stats
* helper `overlay_bbox()` overlays the rotated‑back bbox for visual sanity checks


In [1]:
import cv2, os, math, sys
from pathlib import Path
from typing import List, Tuple
import numpy as np
from tqdm import tqdm
from pathlib import Path
from typing import List, Dict, Any
import os, json, shutil, random, math, datetime as dt
import pandas as pd


VERBOSE = True

def debug(msg: str, level: str = 'INFO') -> None:
    if not VERBOSE:
        return
    colours = {'INFO': '\033[94m', 'WARN': '\033[93m', 'ERR': '\033[91m'}
    print(f"{colours.get(level, '')}[{level}] {msg}\033[0m")

## 1 · Configuration

In [2]:
SRC_IMG_DIR         = Path('../data/rotation/batches/batch_20250703_01/images/default')
SRC_ANNOTATION_PATH = Path('../data/rotation/batches/batch_20250703_01/annotations/instances_default.json')

DEST_IMG_DIR        = Path('../data/rotation/batches/batch_20250703_01/images/boxes')
DEST_IMG_DIR.mkdir(parents=True, exist_ok=True)

ANGLES: List[int]   = [0, 45, 90, 180, 270, 360]

debug('Config loaded.')

[INFO] Config loaded.


## 2 · COCO helpers & utils

In [ ]:

def load_coco(json_path: Path) -> Dict[str, Any]:
    with open(json_path, 'r', encoding='utf-8') as f:
        coco = json.load(f)
    return coco

    

def create_obb_tuple(anns):
    bbox = anns.get("bbox", "No bbox found")

    if(len(bbox) == 4):    
        x, y, w, h = anns["bbox"]
        cx = x + (w/2)
        cy = y + (h/2)
        angle = anns["attributes"].get("rotation", 0.0)
        obb_list = [cx, cy, w, h, angle]
        anns["bbox"] = obb_list
    else: 
        #print(f"type = {type(bbox)}, length = {len(bbox) if hasattr(bbox, '__len__') else 'N/A'}, bbox: {bbox}")
        print("Weirdle after every element is on 5 tuples it starts to iterate again")



def replace_obb(coco):
    for anns in coco['annotations']:
        create_obb_tuple(anns)
        
    json_object = json.dumps(coco)
    with open("../data/rotation/batches/batch_20250703_01/annotations/instances_updated_g.json", mode="w") as file:
        file.write(json_object)
              
        
        
    

## Debug

In [ ]:
def lookAtCoco(json_path: Path):
    coco = load_coco(json_path)
    print(f"Coco {coco}")
    print(f"Keys {coco.keys()}")
    print(f"Values {coco.values()}")
    print(f"Items {coco.items()}")

    print(f"Images      : {(coco['images'])}")
    print(f"Annotations : {(coco['annotations'])}")
    print(f"Categories  : {(coco['categories'])}\n")
    
    
    
    
def debug_bbox(coco):
    for i, anns in enumerate(coco['annotations']):
        bbox = anns.get("bbox", "No bbox found")
        print(f"Annotation {i}: bbox = {bbox}, type = {type(bbox)}, length = {len(bbox) if hasattr(bbox, '__len__') else 'N/A'}")

In [ ]:
coco = load_coco(json_path=SRC_ANNOTATION_PATH)

Annotation 0: bbox = [2434.51, 533.13, 35.37, 32.47], type = <class 'list'>, length = 4
Annotation 1: bbox = [1165.9, 1001.1, 49.4, 18.9], type = <class 'list'>, length = 4
Annotation 2: bbox = [1165.7, 1021.8, 49.74, 19.2], type = <class 'list'>, length = 4
Annotation 3: bbox = [2234.5, 1021.9, 34.1, 19.3], type = <class 'list'>, length = 4
Annotation 4: bbox = [2175.8, 1006.5, 47.5, 37.8], type = <class 'list'>, length = 4
Annotation 5: bbox = [1242.2, 1005.2, 19.7, 31.8], type = <class 'list'>, length = 4
Annotation 6: bbox = [1065.3, 1003.6, 92.5, 41.0], type = <class 'list'>, length = 4
Annotation 7: bbox = [2454.86, 527.38, 146.24, 38.46], type = <class 'list'>, length = 4
Annotation 8: bbox = [2400.6, 1805.7, 267.7, 14.3], type = <class 'list'>, length = 4
Annotation 9: bbox = [2477.8, 1754.0, 211.6, 16.0], type = <class 'list'>, length = 4
Annotation 10: bbox = [2785.9, 1710.8, 221.2, 17.1], type = <class 'list'>, length = 4
Annotation 11: bbox = [289.5, 1471.5, 23.1, 10.1], ty

In [ ]:

debug_bbox(coco)

[{'id': 1, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 1148.4638999999975, 'bbox': [2452.195, 549.365, 35.37, 32.47, 314.6], 'iscrowd': 0, 'attributes': {'occluded': False, 'rotation': 314.6}}, {'id': 2, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 933.6599999999963, 'bbox': [1190.6000000000001, 1010.5500000000001, 49.4, 18.9, 0.0], 'iscrowd': 0, 'attributes': {'occluded': False, 'rotation': 0.0}}, {'id': 3, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 955.0080000000024, 'bbox': [1190.57, 1031.3999999999999, 49.74, 19.2, 0.0], 'iscrowd': 0, 'attributes': {'occluded': False, 'rotation': 0.0}}, {'id': 4, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 658.1300000000006, 'bbox': [2251.55, 1031.55, 34.1, 19.3, 0.0], 'iscrowd': 0, 'attributes': {'occluded': False, 'rotation': 0.0}}, {'id': 5, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 1795.4999999999977, 'bbox': [2199.55, 1025.4, 47.5, 37.8, 0.0], 'iscrowd': 0, 

In [139]:
lookAtCoco(json_path=SRC_ANNOTATION_PATH)

Coco {'licenses': [{'name': '', 'id': 0, 'url': ''}], 'info': {'contributor': '', 'date_created': '', 'description': '', 'url': '', 'version': '', 'year': ''}, 'categories': [{'id': 1, 'name': 'isOk', 'supercategory': ''}, {'id': 2, 'name': 'inner-edge-', 'supercategory': ''}, {'id': 3, 'name': 'additional-infoblock', 'supercategory': ''}, {'id': 4, 'name': 'inner-edge-tolerance', 'supercategory': ''}, {'id': 5, 'name': 'infoblock', 'supercategory': ''}, {'id': 6, 'name': 'gdt', 'supercategory': ''}, {'id': 7, 'name': 'text', 'supercategory': ''}, {'id': 8, 'name': 'additional infoblock', 'supercategory': ''}, {'id': 9, 'name': 'surface-roughness', 'supercategory': ''}, {'id': 10, 'name': 'welding_symbol', 'supercategory': ''}, {'id': 11, 'name': 'infoBlock', 'supercategory': ''}, {'id': 12, 'name': 'general-chamfer', 'supercategory': ''}, {'id': 13, 'name': 'drawing-area', 'supercategory': ''}], 'images': [{'id': 1, 'width': 3055, 'height': 2160, 'file_name': '10000.png', 'license': 0

In [152]:
new_obb = replace_obb(coco)

type = <class 'list'>, length = 5, bbox: [2452.195, 549.365, 35.37, 32.47, 314.6]
type = <class 'list'>, length = 5, bbox: [1190.6000000000001, 1010.5500000000001, 49.4, 18.9, 0.0]
type = <class 'list'>, length = 5, bbox: [1190.57, 1031.3999999999999, 49.74, 19.2, 0.0]
type = <class 'list'>, length = 5, bbox: [2251.55, 1031.55, 34.1, 19.3, 0.0]
type = <class 'list'>, length = 5, bbox: [2199.55, 1025.4, 47.5, 37.8, 0.0]
type = <class 'list'>, length = 5, bbox: [1252.05, 1021.1, 19.7, 31.8, 0.0]
type = <class 'list'>, length = 5, bbox: [1111.55, 1024.1, 92.5, 41.0, 0.0]
type = <class 'list'>, length = 5, bbox: [2527.98, 546.61, 146.24, 38.46, 314.9]
type = <class 'list'>, length = 5, bbox: [2534.45, 1812.8500000000001, 267.7, 14.3, 0.0]
type = <class 'list'>, length = 5, bbox: [2583.6000000000004, 1762.0, 211.6, 16.0, 0.0]
type = <class 'list'>, length = 5, bbox: [2896.5, 1719.35, 221.2, 17.1, 0.0]
type = <class 'list'>, length = 5, bbox: [301.05, 1476.55, 23.1, 10.1, 270.0]
type = <clas

In [153]:
print(coco["annotations"])


[{'id': 1, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 1148.4638999999975, 'bbox': [2452.195, 549.365, 35.37, 32.47, 314.6], 'iscrowd': 0, 'attributes': {'occluded': False, 'rotation': 314.6}}, {'id': 2, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 933.6599999999963, 'bbox': [1190.6000000000001, 1010.5500000000001, 49.4, 18.9, 0.0], 'iscrowd': 0, 'attributes': {'occluded': False, 'rotation': 0.0}}, {'id': 3, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 955.0080000000024, 'bbox': [1190.57, 1031.3999999999999, 49.74, 19.2, 0.0], 'iscrowd': 0, 'attributes': {'occluded': False, 'rotation': 0.0}}, {'id': 4, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 658.1300000000006, 'bbox': [2251.55, 1031.55, 34.1, 19.3, 0.0], 'iscrowd': 0, 'attributes': {'occluded': False, 'rotation': 0.0}}, {'id': 5, 'image_id': 1, 'category_id': 7, 'segmentation': [], 'area': 1795.4999999999977, 'bbox': [2199.55, 1025.4, 47.5, 37.8, 0.0], 'iscrowd': 0, 

## 3 · Geometry with loss stats

In [6]:
def rectify_patch(img, cx, cy, w, h, theta):
    debug(f'Rectify: centre=({cx:.1f},{cy:.1f}) w={w:.1f} h={h:.1f} θ={theta:.1f}')
    
    M = cv2.getRotationMatrix2D((cx, cy), -theta, 1.0)
    rot = cv2.warpAffine(img, M, (img.shape[1], img.shape[0]), flags=cv2.INTER_LINEAR)

    half_w, half_h = (w)/2, (h)/2
    x0, y0 = int(cx - half_w), int(cy - half_h)
    x1, y1 = int(cx + half_w), int(cy + half_h)

    lost_w = lost_h = 0
    if x0 < 0: lost_w += -x0; x0 = 0
    if y0 < 0: lost_h += -y0; y0 = 0
    if x1 > rot.shape[1]: lost_w += x1-rot.shape[1]; x1 = rot.shape[1]
    if y1 > rot.shape[0]: lost_h += y1-rot.shape[0]; y1 = rot.shape[0]

    patch = rot[y0:y1, x0:x1].copy()
    exp_w, exp_h = int(w), int(h)
    debug(f'Patch {patch.shape} expected≈({exp_h},{exp_w}) lost ({lost_w}px, {lost_h}px)')
    return patch, (lost_w, lost_h)

In [8]:
image_1 = '../data/rotation/batches/batch_20250703_01/images/default/10000.png'

rectify_patch(image_1, 2452.195, 549.365, 35.37, 32.47, 314.6)

[INFO] Rectify: centre=(2452.2,549.4) w=35.4 h=32.5 θ=314.6


AttributeError: 'str' object has no attribute 'shape'

In [ ]:
rectify_patch()

In [10]:
def rotate_patch(patch, angle):
    h, w = patch.shape[:2]
    M = cv2.getRotationMatrix2D((w/2, h/2), angle, 1.0)
    cos, sin = abs(M[0,0]), abs(M[0,1])
    new_w, new_h = int(h*sin + w*cos), int(h*cos + w*sin)
    M[0,2] += new_w/2 - w/2
    M[1,2] += new_h/2 - h/2
    return cv2.warpAffine(patch, M, (new_w, new_h), flags=cv2.INTER_LINEAR, borderValue=255)

## 4 · Save helper

## 5 · Overlay helper (optional)

## 6 · Main loop with extra prints

In [ ]:
def process_dataset(src_img_dir: Path, coco_json: Path, dest_img_dir: Path,
                    angles: List[int] = ANGLES, every: int = 200):
    coco = load_coco(coco_json)
    


## 7 · Interactive inspect()

## 8 · Smoke test

## 9 · Run full dataset

In [12]:
# VERBOSE = False  # uncomment for speed
# process_dataset(SRC_IMG_DIR, SRC_ANNOTATION_PATH, DEST_IMG_DIR)